In [1]:
cd ..

/Users/muhammadfarooq/Codebase/thesis-experiment/Pith2Bark


In [2]:
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
import warnings
warnings.filterwarnings("ignore")

import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

import tensorflow as tf

from keras.models import Sequential
from keras.layers import Dense, Dropout

from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.metrics import balanced_accuracy_score

from src.winner import winner_model_rings
from src.damage import merge_df
from src.damage import read_damage_min_max
from src.damage import read_damage_mean

# Damage Dataset

In [3]:
mse_url = "output/ringsranking_mse_sixteen.csv"
rings_url = "output/ringsranking_rings_sixteen.csv"
df_ringsranking_sixteen = winner_model_rings(mse_url, rings_url)

mse_url = "output/ringsranking_mse_thirtytwo.csv"
rings_url = "output/ringsranking_rings_thirtytwo.csv"
df_ringsranking_thirtytwo = winner_model_rings(mse_url, rings_url)

Polar Pith Canny(blur otsu) 12.829318845239923 (subseq)
Polar Pith Canny(blur otsu) 12.88055458721076 (subseq)


In [4]:
mse_url = "output/pine_mse_sixteen.csv"
rings_url = "output/pine_rings_sixteen.csv"
df_pine_sixteen = winner_model_rings(mse_url, rings_url)

mse_url = "output/pine_mse_thirtytwo.csv"
rings_url = "output/pine_rings_thirtytwo.csv"
df_pine_thirtytwo = winner_model_rings(mse_url, rings_url)

Polar Pith Canny(blur triangle) 19.888455438324574 (peaks)
Polar Pith Canny(blur triangle) 19.591747084408897 (peaks)


In [5]:
mse_url = "output/fur_mse_sixteen.csv"
rings_url = "output/fur_rings_sixteen.csv"
df_fur_sixteen = winner_model_rings(mse_url, rings_url)

mse_url = "output/fur_mse_thirtytwo.csv"
rings_url = "output/fur_rings_thirtytwo.csv"
df_fur_thirtytwo = winner_model_rings(mse_url, rings_url)

Polar Pith Canny(blur triangle) 13.428984012468806 (peaks)
Polar Pith Canny(blur triangle) 13.688767879960144 (peaks)


In [6]:
mse_url = "output/tracy_mse_sixteen.csv"
rings_url = "output/tracy_rings_sixteen.csv"
df_tracy_sixteen = winner_model_rings(mse_url, rings_url)

mse_url = "output/tracy_mse_thirtytwo.csv"
rings_url = "output/tracy_rings_thirtytwo.csv"
df_tracy_thirtytwo = winner_model_rings(mse_url, rings_url)

Polar Canny(triangle) 39.683736416974455 (peaks)
Polar Pith Canny(triangle) 39.48914666858598 (peaks)


In [7]:
mse_url = "output/data_mse_sixteen.csv"
rings_url = "output/data_rings_sixteen.csv"
df_data_sixteen = winner_model_rings(mse_url, rings_url)

mse_url = "output/data_mse_thirtytwo.csv"
rings_url = "output/data_rings_thirtytwo.csv"
df_data_thirtytwo = winner_model_rings(mse_url, rings_url)

Canny(triangle) 18.789996216404624 (subseq)
Canny(triangle) 18.871624925897343 (subseq)


In [8]:
#damage
damage_sixteen_url = "damage/damage_sixteen.csv"
damage_thirtytwo_url = "damage/damage_thirtytwo.csv"

#merge
df_merge_sixteen = merge_df(df_ringsranking_sixteen, df_pine_sixteen, df_fur_sixteen, df_tracy_sixteen, df_data_sixteen)
df_merge_thirtytwo = merge_df(df_ringsranking_thirtytwo, df_pine_thirtytwo, df_fur_thirtytwo, df_tracy_thirtytwo, df_data_thirtytwo)

df_damage_sixteen_min_max = read_damage_min_max(damage_sixteen_url, df_merge_sixteen)
df_damage_thirtytwo_min_max = read_damage_min_max(damage_thirtytwo_url, df_merge_thirtytwo)

df_damage_sixteen_mean = read_damage_mean(damage_sixteen_url, df_merge_sixteen)
df_damage_thirtytwo_mean = read_damage_mean(damage_thirtytwo_url, df_merge_thirtytwo)

In [9]:
#df_damage_sixteen_min_max

In [10]:
#df_damage_thirtytwo_min_max

In [11]:
#df_damage_sixteen_mean

In [12]:
#df_damage_thirtytwo_mean

In [13]:
#STOP

# Config

In [14]:
training_percent = 0.9

epochs, batch_size = 50, 32
kf = KFold(n_splits=3, shuffle=True, random_state=42)

# mode = max for monitro val_accuracy and val_prc
early_stopping = tf.keras.callbacks.EarlyStopping(
    monitor='val_loss', 
    patience=10,
    restore_best_weights=True)

METRICS = [
    tf.keras.metrics.TruePositives(name='tp'),
    tf.keras.metrics.FalsePositives(name='fp'),
    tf.keras.metrics.TrueNegatives(name='tn'),
    tf.keras.metrics.FalseNegatives(name='fn'), 
    tf.keras.metrics.BinaryAccuracy(name='accuracy'),
    tf.keras.metrics.Precision(name='precision'),
    tf.keras.metrics.Recall(name='recall'),
    tf.keras.metrics.AUC(name='auc'),
    tf.keras.metrics.AUC(name='prc', curve='PR'), # precision-recall curve
]

#columns to drop
columns = ['image', 'algo']

In [15]:
def heat_map(_cm):
    # plot confusion matrix as heatmap
    
    labels = ['Not Damage', 'Damaged']
    
    # Set up the matplotlib figure
    plt.figure(figsize=(4, 3))
    
    # Generate a custom diverging colormap
    cmap = sns.diverging_palette(230, 20, as_cmap=True)
    
    sns.heatmap(_cm, annot=True, cmap=cmap, xticklabels=labels, yticklabels=labels)
    plt.xlabel('Predicted labels')
    plt.ylabel('True labels')
    plt.show()

In [16]:
units = [32]
activations = ['relu', 'tanh', 'sigmoid']
kernel_size = [3, 5]
learning_rate = [0.001, 0.0001, 0.00001]
optimizer = ['Adam', 'RMSprop', 'Nadam']
dropout = [0.1, 0.2, 0.3]

# Model

In [17]:
class Baseline():
    def __init__(self, _input_dim, unit, activation, kernel_size, learning_rate, optimizer, dropout, metrics=METRICS):
        # Define the model architecture
        model = Sequential()
        
        # hidden layer
        model.add(Dense(unit, activation=activation, input_dim=_input_dim))
        model.add(Dropout(dropout))
        
        # hidden layer
        model.add(Dense(unit, activation=activation))
        model.add(Dropout(dropout))
        
        # hidden layer
        model.add(Dense(unit, activation=activation))
        model.add(Dropout(dropout))
        
        # hidden layer
        model.add(Dense(unit, activation=activation))
        model.add(Dropout(dropout))
        
        # output layer
        model.add(Dense(1, activation='sigmoid'))

        if optimizer == 'Adam':
            ops = tf.keras.optimizers.Adam(learning_rate=learning_rate)
        elif optimizer == 'RMSprop':
            ops = tf.keras.optimizers.RMSprop(learning_rate=learning_rate)
        elif optimizer == 'Nadam':
            ops = tf.keras.optimizers.Nadam(learning_rate=learning_rate)
            
        # Compile the model
        model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])

        self.model = model
        
    def train(self, X_train, y_train, X_val, y_val, epochs, batch_size):
        history = self.model.fit(X_train, y_train, validation_data=(X_val, y_val), epochs=epochs, batch_size=batch_size, callbacks=[early_stopping], verbose=2)
        return history

    def evaluate(self, X_test, y_test):
        results = self.model.evaluate(X_test, y_test, verbose=0)
        return results

    def predict(self, X): #X_train X_test
        predictions = self.model.predict(X)
        return predictions
    
    def summary(self):
        self.model.summary()
        
    def metrics_names(self):
        return self.model.metrics_names

# 1 Prepare dataset

In [18]:
df = df_damage_sixteen_min_max.drop(columns=columns)

X = df.drop(columns=['Damage'])
y = df['Damage']

# split the data into a holdout set and the rest for K-Fold cross-validation
X_train, X_holdout, y_train, y_holdout = train_test_split(X, y, train_size=training_percent, random_state=42)

In [19]:
# Initialize StandardScaler
scaler = StandardScaler()

# Fit scaler on training data
scaler.fit(X_train)

# Transform both training and test data
X_train_scaled = scaler.transform(X_train)
X_holdout_scaled = scaler.transform(X_holdout)

In [20]:
best_acc = 0.0
baseline_values = { 'units': 0, 'activation': '', 'kernel_size': 0, 'learning_rate' : 0.0, 'optimizer': '', 'dropout': 0.0 }

In [21]:
input_dim = X_train.shape[1]

In [22]:
for u in units:
    for a in activations:
        for k in kernel_size:
            for l in learning_rate:
                for o in optimizer:
                    for d in dropout:
                        print('\nUnits:', u, 'Activation:', a, 'Kernel size:', k, 'Learning rate:', l, 'Optimizer:', o, 'Dropout:', d)
                        for train_index, val_index in kf.split(X_train_scaled):
                            # split the dataset into training and validation sets for this fold
                            X_train_kf, X_val_kf = X_train_scaled[train_index], X_train_scaled[val_index]
                            y_train_kf, y_val_kf = y_train.iloc[train_index], y_train.iloc[val_index]

                            model = Baseline(input_dim, u, a, k, l, o, d)

                            history = model.train(X_train_kf, y_train_kf, X_val_kf, y_val_kf, epochs, batch_size)
                            if (history.history['val_accuracy'][-1] > best_acc):
                                best_acc = history.history['val_accuracy'][-1]
                                baseline_values = { 'units': u, 'activation': a, 'kernel_size': k, 'learning_rate' : l, 'optimizer': o, 'dropout': d }


Units: 32 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: Adam Dropout: 0.1
Epoch 1/50
3/3 - 2s - loss: 0.7174 - accuracy: 0.3750 - val_loss: 0.6504 - val_accuracy: 0.4222 - 2s/epoch - 575ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6741 - accuracy: 0.3977 - val_loss: 0.6268 - val_accuracy: 0.6889 - 37ms/epoch - 12ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6346 - accuracy: 0.5000 - val_loss: 0.6062 - val_accuracy: 0.7778 - 32ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6005 - accuracy: 0.6818 - val_loss: 0.5849 - val_accuracy: 0.8889 - 33ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0.5859 - accuracy: 0.7841 - val_loss: 0.5630 - val_accuracy: 0.9333 - 36ms/epoch - 12ms/step
Epoch 6/50
3/3 - 0s - loss: 0.5633 - accuracy: 0.8295 - val_loss: 0.5403 - val_accuracy: 0.9111 - 52ms/epoch - 17ms/step
Epoch 7/50
3/3 - 0s - loss: 0.5420 - accuracy: 0.8636 - val_loss: 0.5189 - val_accuracy: 0.9111 - 34ms/epoch - 11ms/step
Epoch 8/50
3/3 - 0s - loss: 0.5240 - accuracy: 0.8636 - val_l

Epoch 11/50
3/3 - 0s - loss: 0.3978 - accuracy: 0.8876 - val_loss: 0.2746 - val_accuracy: 0.9318 - 44ms/epoch - 15ms/step
Epoch 12/50
3/3 - 0s - loss: 0.3895 - accuracy: 0.8652 - val_loss: 0.2466 - val_accuracy: 0.9318 - 46ms/epoch - 15ms/step
Epoch 13/50
3/3 - 0s - loss: 0.3469 - accuracy: 0.8764 - val_loss: 0.2220 - val_accuracy: 0.9318 - 48ms/epoch - 16ms/step
Epoch 14/50
3/3 - 0s - loss: 0.3450 - accuracy: 0.8876 - val_loss: 0.2011 - val_accuracy: 0.9318 - 40ms/epoch - 13ms/step
Epoch 15/50
3/3 - 0s - loss: 0.3474 - accuracy: 0.8764 - val_loss: 0.1853 - val_accuracy: 0.9318 - 55ms/epoch - 18ms/step
Epoch 16/50
3/3 - 0s - loss: 0.3195 - accuracy: 0.8764 - val_loss: 0.1729 - val_accuracy: 0.9318 - 56ms/epoch - 19ms/step
Epoch 17/50
3/3 - 0s - loss: 0.3233 - accuracy: 0.8764 - val_loss: 0.1632 - val_accuracy: 0.9091 - 43ms/epoch - 14ms/step
Epoch 18/50
3/3 - 0s - loss: 0.2986 - accuracy: 0.8876 - val_loss: 0.1564 - val_accuracy: 0.9318 - 43ms/epoch - 14ms/step
Epoch 19/50
3/3 - 0s - l

Epoch 28/50
3/3 - 0s - loss: 0.1819 - accuracy: 0.9318 - val_loss: 0.3249 - val_accuracy: 0.9111 - 34ms/epoch - 11ms/step
Epoch 29/50
3/3 - 0s - loss: 0.2218 - accuracy: 0.9091 - val_loss: 0.3298 - val_accuracy: 0.9111 - 38ms/epoch - 13ms/step
Epoch 30/50
3/3 - 0s - loss: 0.2039 - accuracy: 0.9318 - val_loss: 0.3349 - val_accuracy: 0.9111 - 40ms/epoch - 13ms/step
Epoch 1/50
3/3 - 1s - loss: 0.7486 - accuracy: 0.3933 - val_loss: 0.6846 - val_accuracy: 0.4545 - 1s/epoch - 485ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6751 - accuracy: 0.5056 - val_loss: 0.6603 - val_accuracy: 0.5909 - 42ms/epoch - 14ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6441 - accuracy: 0.5843 - val_loss: 0.6381 - val_accuracy: 0.8182 - 33ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6283 - accuracy: 0.6292 - val_loss: 0.6157 - val_accuracy: 0.8409 - 33ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6215 - accuracy: 0.6966 - val_loss: 0.5936 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 6/50
3/3 - 0s - loss: 0.

Epoch 34/50
3/3 - 0s - loss: 0.2980 - accuracy: 0.9213 - val_loss: 0.1578 - val_accuracy: 0.9091 - 43ms/epoch - 14ms/step
Epoch 35/50
3/3 - 0s - loss: 0.3075 - accuracy: 0.8989 - val_loss: 0.1571 - val_accuracy: 0.9091 - 44ms/epoch - 15ms/step
Epoch 36/50
3/3 - 0s - loss: 0.2728 - accuracy: 0.8989 - val_loss: 0.1567 - val_accuracy: 0.9091 - 38ms/epoch - 13ms/step
Epoch 37/50
3/3 - 0s - loss: 0.2550 - accuracy: 0.9213 - val_loss: 0.1562 - val_accuracy: 0.9091 - 40ms/epoch - 13ms/step
Epoch 38/50
3/3 - 0s - loss: 0.3222 - accuracy: 0.8989 - val_loss: 0.1569 - val_accuracy: 0.9091 - 39ms/epoch - 13ms/step
Epoch 39/50
3/3 - 0s - loss: 0.3120 - accuracy: 0.8989 - val_loss: 0.1557 - val_accuracy: 0.9091 - 37ms/epoch - 12ms/step
Epoch 40/50
3/3 - 0s - loss: 0.2830 - accuracy: 0.8989 - val_loss: 0.1550 - val_accuracy: 0.9091 - 39ms/epoch - 13ms/step
Epoch 41/50
3/3 - 0s - loss: 0.2317 - accuracy: 0.8989 - val_loss: 0.1536 - val_accuracy: 0.9091 - 38ms/epoch - 13ms/step
Epoch 42/50
3/3 - 0s - l

Epoch 12/50
3/3 - 0s - loss: 0.5938 - accuracy: 0.7865 - val_loss: 0.5732 - val_accuracy: 0.8409 - 33ms/epoch - 11ms/step
Epoch 13/50
3/3 - 0s - loss: 0.6013 - accuracy: 0.7640 - val_loss: 0.5633 - val_accuracy: 0.8409 - 33ms/epoch - 11ms/step
Epoch 14/50
3/3 - 0s - loss: 0.5573 - accuracy: 0.8652 - val_loss: 0.5530 - val_accuracy: 0.8409 - 36ms/epoch - 12ms/step
Epoch 15/50
3/3 - 0s - loss: 0.5359 - accuracy: 0.7865 - val_loss: 0.5428 - val_accuracy: 0.8409 - 32ms/epoch - 11ms/step
Epoch 16/50
3/3 - 0s - loss: 0.5472 - accuracy: 0.8202 - val_loss: 0.5326 - val_accuracy: 0.8409 - 36ms/epoch - 12ms/step
Epoch 17/50
3/3 - 0s - loss: 0.5853 - accuracy: 0.8315 - val_loss: 0.5227 - val_accuracy: 0.8409 - 33ms/epoch - 11ms/step
Epoch 18/50
3/3 - 0s - loss: 0.5283 - accuracy: 0.8315 - val_loss: 0.5121 - val_accuracy: 0.8409 - 35ms/epoch - 12ms/step
Epoch 19/50
3/3 - 0s - loss: 0.5258 - accuracy: 0.8764 - val_loss: 0.5015 - val_accuracy: 0.8409 - 34ms/epoch - 11ms/step
Epoch 20/50
3/3 - 0s - l

...

Epoch 1/50
3/3 - 2s - loss: 0.6452 - accuracy: 0.6705 - val_loss: 0.7003 - val_accuracy: 0.5778 - 2s/epoch - 762ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6662 - accuracy: 0.6705 - val_loss: 0.6976 - val_accuracy: 0.5778 - 38ms/epoch - 13ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6615 - accuracy: 0.6705 - val_loss: 0.6970 - val_accuracy: 0.5778 - 37ms/epoch - 12ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6359 - accuracy: 0.6705 - val_loss: 0.6965 - val_accuracy: 0.5778 - 37ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6365 - accuracy: 0.6705 - val_loss: 0.6968 - val_accuracy: 0.5778 - 36ms/epoch - 12ms/step
Epoch 6/50
3/3 - 0s - loss: 0.6278 - accuracy: 0.6818 - val_loss: 0.6964 - val_accuracy: 0.5778 - 36ms/epoch - 12ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6251 - accuracy: 0.6705 - val_loss: 0.6949 - val_accuracy: 0.5778 - 37ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.6319 - accuracy: 0.6591 - val_loss: 0.6933 - val_accuracy: 0.5778 - 35ms/epoch - 12ms/step
Epoch 9/50
3/3 - 0s - loss: 0.628

Epoch 19/50
3/3 - 0s - loss: 0.6478 - accuracy: 0.6517 - val_loss: 0.6577 - val_accuracy: 0.6136 - 34ms/epoch - 11ms/step
Epoch 20/50
3/3 - 0s - loss: 0.6661 - accuracy: 0.6517 - val_loss: 0.6560 - val_accuracy: 0.6136 - 34ms/epoch - 11ms/step
Epoch 21/50
3/3 - 0s - loss: 0.6282 - accuracy: 0.6517 - val_loss: 0.6539 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 22/50
3/3 - 0s - loss: 0.6451 - accuracy: 0.6404 - val_loss: 0.6515 - val_accuracy: 0.6136 - 34ms/epoch - 11ms/step
Epoch 23/50
3/3 - 0s - loss: 0.6362 - accuracy: 0.6517 - val_loss: 0.6490 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 24/50
3/3 - 0s - loss: 0.6247 - accuracy: 0.6404 - val_loss: 0.6458 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 25/50
3/3 - 0s - loss: 0.6330 - accuracy: 0.6629 - val_loss: 0.6423 - val_accuracy: 0.6136 - 34ms/epoch - 11ms/step
Epoch 26/50
3/3 - 0s - loss: 0.6256 - accuracy: 0.6517 - val_loss: 0.6389 - val_accuracy: 0.6136 - 34ms/epoch - 11ms/step
Epoch 27/50
3/3 - 0s - l

Epoch 37/50
3/3 - 0s - loss: 0.5727 - accuracy: 0.7640 - val_loss: 0.4435 - val_accuracy: 0.9773 - 34ms/epoch - 11ms/step
Epoch 38/50
3/3 - 0s - loss: 0.5318 - accuracy: 0.7978 - val_loss: 0.4306 - val_accuracy: 0.9545 - 34ms/epoch - 11ms/step
Epoch 39/50
3/3 - 0s - loss: 0.5201 - accuracy: 0.8315 - val_loss: 0.4173 - val_accuracy: 0.9773 - 34ms/epoch - 11ms/step
Epoch 40/50
3/3 - 0s - loss: 0.5247 - accuracy: 0.7865 - val_loss: 0.4031 - val_accuracy: 0.9773 - 34ms/epoch - 11ms/step
Epoch 41/50
3/3 - 0s - loss: 0.4849 - accuracy: 0.8652 - val_loss: 0.3899 - val_accuracy: 0.9773 - 33ms/epoch - 11ms/step
Epoch 42/50
3/3 - 0s - loss: 0.4857 - accuracy: 0.8764 - val_loss: 0.3765 - val_accuracy: 0.9773 - 33ms/epoch - 11ms/step
Epoch 43/50
3/3 - 0s - loss: 0.4729 - accuracy: 0.8876 - val_loss: 0.3626 - val_accuracy: 0.9773 - 34ms/epoch - 11ms/step
Epoch 44/50
3/3 - 0s - loss: 0.4663 - accuracy: 0.8652 - val_loss: 0.3485 - val_accuracy: 0.9773 - 34ms/epoch - 11ms/step
Epoch 45/50
3/3 - 0s - l

Epoch 42/50
3/3 - 0s - loss: 0.5172 - accuracy: 0.7753 - val_loss: 0.5386 - val_accuracy: 0.6136 - 36ms/epoch - 12ms/step
Epoch 43/50
3/3 - 0s - loss: 0.5085 - accuracy: 0.7416 - val_loss: 0.5274 - val_accuracy: 0.7500 - 34ms/epoch - 11ms/step
Epoch 44/50
3/3 - 0s - loss: 0.5276 - accuracy: 0.7528 - val_loss: 0.5157 - val_accuracy: 0.7727 - 32ms/epoch - 11ms/step
Epoch 45/50
3/3 - 0s - loss: 0.4948 - accuracy: 0.8090 - val_loss: 0.5044 - val_accuracy: 0.8182 - 34ms/epoch - 11ms/step
Epoch 46/50
3/3 - 0s - loss: 0.4665 - accuracy: 0.7865 - val_loss: 0.4931 - val_accuracy: 0.8182 - 32ms/epoch - 11ms/step
Epoch 47/50
3/3 - 0s - loss: 0.4537 - accuracy: 0.8539 - val_loss: 0.4816 - val_accuracy: 0.8182 - 34ms/epoch - 11ms/step
Epoch 48/50
3/3 - 0s - loss: 0.4263 - accuracy: 0.8427 - val_loss: 0.4709 - val_accuracy: 0.8182 - 35ms/epoch - 12ms/step
Epoch 49/50
3/3 - 0s - loss: 0.4216 - accuracy: 0.8764 - val_loss: 0.4601 - val_accuracy: 0.8636 - 34ms/epoch - 11ms/step
Epoch 50/50
3/3 - 0s - l

Epoch 35/50
3/3 - 0s - loss: 0.5977 - accuracy: 0.7079 - val_loss: 0.6326 - val_accuracy: 0.6136 - 38ms/epoch - 13ms/step
Epoch 36/50
3/3 - 0s - loss: 0.6284 - accuracy: 0.6292 - val_loss: 0.6296 - val_accuracy: 0.6136 - 55ms/epoch - 18ms/step
Epoch 37/50
3/3 - 0s - loss: 0.6378 - accuracy: 0.6742 - val_loss: 0.6263 - val_accuracy: 0.6136 - 41ms/epoch - 14ms/step
Epoch 38/50
3/3 - 0s - loss: 0.6170 - accuracy: 0.6629 - val_loss: 0.6231 - val_accuracy: 0.6136 - 45ms/epoch - 15ms/step
Epoch 39/50
3/3 - 0s - loss: 0.6115 - accuracy: 0.6629 - val_loss: 0.6201 - val_accuracy: 0.6136 - 41ms/epoch - 14ms/step
Epoch 40/50
3/3 - 0s - loss: 0.6117 - accuracy: 0.6966 - val_loss: 0.6169 - val_accuracy: 0.6136 - 37ms/epoch - 12ms/step
Epoch 41/50
3/3 - 0s - loss: 0.5886 - accuracy: 0.6517 - val_loss: 0.6127 - val_accuracy: 0.6136 - 34ms/epoch - 11ms/step
Epoch 42/50
3/3 - 0s - loss: 0.6628 - accuracy: 0.5730 - val_loss: 0.6079 - val_accuracy: 0.6136 - 32ms/epoch - 11ms/step
Epoch 43/50
3/3 - 0s - l

In [23]:
print(best_acc)
print(baseline_values)

1.0
{'units': 32, 'activation': 'relu', 'kernel_size': 3, 'learning_rate': 0.001, 'optimizer': 'RMSprop', 'dropout': 0.1}


In [24]:
#STOP

# 2 Prepare dataset

In [25]:
df = df_damage_thirtytwo_min_max.drop(columns=columns)

X = df.drop(columns=['Damage'])
y = df['Damage']

# split the data into a holdout set and the rest for K-Fold cross-validation
X_train, X_holdout, y_train, y_holdout = train_test_split(X, y, train_size=training_percent, random_state=42)

In [26]:
# Initialize StandardScaler
scaler = StandardScaler()

# Fit scaler on training data
scaler.fit(X_train)

# Transform both training and test data
X_train_scaled = scaler.transform(X_train)
X_holdout_scaled = scaler.transform(X_holdout)

In [27]:
best_acc = 0.0
baseline_values = { 'units': 0, 'activation': '', 'kernel_size': 0, 'learning_rate' : 0.0, 'optimizer': '', 'dropout': 0.0 }

In [28]:
input_dim = X_train.shape[1]

In [29]:
for u in units:
    for a in activations:
        for k in kernel_size:
            for l in learning_rate:
                for o in optimizer:
                    for d in dropout:
                        print('\nUnits:', u, 'Activation:', a, 'Kernel size:', k, 'Learning rate:', l, 'Optimizer:', o, 'Dropout:', d)
                        for train_index, val_index in kf.split(X_train_scaled):
                            # split the dataset into training and validation sets for this fold
                            X_train_kf, X_val_kf = X_train_scaled[train_index], X_train_scaled[val_index]
                            y_train_kf, y_val_kf = y_train.iloc[train_index], y_train.iloc[val_index]

                            model = Baseline(input_dim, u, a, k, l, o, d)

                            history = model.train(X_train_kf, y_train_kf, X_val_kf, y_val_kf, epochs, batch_size)
                            if (history.history['val_accuracy'][-1] > best_acc):
                                best_acc = history.history['val_accuracy'][-1]
                                baseline_values = { 'units': u, 'activation': a, 'kernel_size': k, 'learning_rate' : l, 'optimizer': o, 'dropout': d }


Units: 32 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: Adam Dropout: 0.1
Epoch 1/50
3/3 - 1s - loss: 0.7596 - accuracy: 0.4091 - val_loss: 0.6487 - val_accuracy: 0.4889 - 1s/epoch - 393ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6735 - accuracy: 0.4659 - val_loss: 0.6063 - val_accuracy: 0.4889 - 35ms/epoch - 12ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6250 - accuracy: 0.5114 - val_loss: 0.5658 - val_accuracy: 0.8222 - 34ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.5982 - accuracy: 0.6932 - val_loss: 0.5267 - val_accuracy: 0.9111 - 37ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0.5727 - accuracy: 0.7841 - val_loss: 0.4861 - val_accuracy: 0.8889 - 34ms/epoch - 11ms/step
Epoch 6/50
3/3 - 0s - loss: 0.5048 - accuracy: 0.8750 - val_loss: 0.4460 - val_accuracy: 0.8889 - 35ms/epoch - 12ms/step
Epoch 7/50
3/3 - 0s - loss: 0.4728 - accuracy: 0.8864 - val_loss: 0.4079 - val_accuracy: 0.8889 - 35ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.4373 - accuracy: 0.8977 - val_l

Epoch 17/50
3/3 - 0s - loss: 0.2526 - accuracy: 0.8989 - val_loss: 0.2454 - val_accuracy: 0.9091 - 34ms/epoch - 11ms/step
Epoch 18/50
3/3 - 0s - loss: 0.2684 - accuracy: 0.8989 - val_loss: 0.2451 - val_accuracy: 0.9091 - 35ms/epoch - 12ms/step
Epoch 19/50
3/3 - 0s - loss: 0.2459 - accuracy: 0.9101 - val_loss: 0.2449 - val_accuracy: 0.9091 - 33ms/epoch - 11ms/step
Epoch 20/50
3/3 - 0s - loss: 0.2792 - accuracy: 0.8989 - val_loss: 0.2448 - val_accuracy: 0.9091 - 34ms/epoch - 11ms/step
Epoch 21/50
3/3 - 0s - loss: 0.2736 - accuracy: 0.8989 - val_loss: 0.2451 - val_accuracy: 0.9091 - 33ms/epoch - 11ms/step
Epoch 22/50
3/3 - 0s - loss: 0.2530 - accuracy: 0.8989 - val_loss: 0.2456 - val_accuracy: 0.9091 - 32ms/epoch - 11ms/step
Epoch 23/50
3/3 - 0s - loss: 0.2454 - accuracy: 0.9101 - val_loss: 0.2459 - val_accuracy: 0.9091 - 34ms/epoch - 11ms/step
Epoch 24/50
3/3 - 0s - loss: 0.2546 - accuracy: 0.9213 - val_loss: 0.2462 - val_accuracy: 0.9091 - 33ms/epoch - 11ms/step
Epoch 25/50
3/3 - 0s - l

Epoch 21/50
3/3 - 0s - loss: 0.2422 - accuracy: 0.9213 - val_loss: 0.3999 - val_accuracy: 0.8182 - 36ms/epoch - 12ms/step
Epoch 22/50
3/3 - 0s - loss: 0.2272 - accuracy: 0.8989 - val_loss: 0.4017 - val_accuracy: 0.8182 - 35ms/epoch - 12ms/step
Epoch 23/50
3/3 - 0s - loss: 0.2582 - accuracy: 0.8989 - val_loss: 0.4037 - val_accuracy: 0.8182 - 34ms/epoch - 11ms/step
Epoch 24/50
3/3 - 0s - loss: 0.1961 - accuracy: 0.9213 - val_loss: 0.4059 - val_accuracy: 0.8182 - 39ms/epoch - 13ms/step
Epoch 1/50
3/3 - 1s - loss: 0.7038 - accuracy: 0.6067 - val_loss: 0.6409 - val_accuracy: 0.7500 - 1s/epoch - 443ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6374 - accuracy: 0.6742 - val_loss: 0.6029 - val_accuracy: 0.8636 - 36ms/epoch - 12ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6198 - accuracy: 0.7079 - val_loss: 0.5636 - val_accuracy: 0.8864 - 34ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.5744 - accuracy: 0.7416 - val_loss: 0.5225 - val_accuracy: 0.9091 - 35ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0

Epoch 35/50
3/3 - 0s - loss: 0.3369 - accuracy: 0.8636 - val_loss: 0.2604 - val_accuracy: 0.8667 - 31ms/epoch - 10ms/step
Epoch 36/50
3/3 - 0s - loss: 0.2666 - accuracy: 0.9091 - val_loss: 0.2612 - val_accuracy: 0.8667 - 32ms/epoch - 11ms/step
Epoch 37/50
3/3 - 0s - loss: 0.2708 - accuracy: 0.9091 - val_loss: 0.2621 - val_accuracy: 0.8667 - 32ms/epoch - 11ms/step
Epoch 38/50
3/3 - 0s - loss: 0.2570 - accuracy: 0.9091 - val_loss: 0.2638 - val_accuracy: 0.8667 - 37ms/epoch - 12ms/step
Epoch 1/50
3/3 - 1s - loss: 0.7388 - accuracy: 0.4831 - val_loss: 0.6466 - val_accuracy: 0.7500 - 1s/epoch - 439ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6906 - accuracy: 0.5506 - val_loss: 0.6200 - val_accuracy: 0.7955 - 39ms/epoch - 13ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6340 - accuracy: 0.6067 - val_loss: 0.5953 - val_accuracy: 0.8182 - 41ms/epoch - 14ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6244 - accuracy: 0.6180 - val_loss: 0.5696 - val_accuracy: 0.8409 - 37ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0

Epoch 35/50
3/3 - 0s - loss: 0.2576 - accuracy: 0.9101 - val_loss: 0.2445 - val_accuracy: 0.9091 - 31ms/epoch - 10ms/step
Epoch 36/50
3/3 - 0s - loss: 0.2640 - accuracy: 0.8989 - val_loss: 0.2459 - val_accuracy: 0.9091 - 30ms/epoch - 10ms/step
Epoch 37/50
3/3 - 0s - loss: 0.2975 - accuracy: 0.8876 - val_loss: 0.2474 - val_accuracy: 0.9091 - 30ms/epoch - 10ms/step
Epoch 38/50
3/3 - 0s - loss: 0.2547 - accuracy: 0.9101 - val_loss: 0.2481 - val_accuracy: 0.9091 - 32ms/epoch - 11ms/step

Units: 32 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: RMSprop Dropout: 0.1
Epoch 1/50
3/3 - 1s - loss: 0.6734 - accuracy: 0.6364 - val_loss: 0.6081 - val_accuracy: 0.8444 - 969ms/epoch - 323ms/step
Epoch 2/50
3/3 - 0s - loss: 0.5822 - accuracy: 0.8409 - val_loss: 0.5396 - val_accuracy: 0.8889 - 32ms/epoch - 11ms/step
Epoch 3/50
3/3 - 0s - loss: 0.5155 - accuracy: 0.8523 - val_loss: 0.4752 - val_accuracy: 0.9111 - 33ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.4694 - accuracy: 0.87

...

Epoch 33/50
3/3 - 0s - loss: 0.5125 - accuracy: 0.8202 - val_loss: 0.5153 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 34/50
3/3 - 0s - loss: 0.4972 - accuracy: 0.8652 - val_loss: 0.5029 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 35/50
3/3 - 0s - loss: 0.4770 - accuracy: 0.9101 - val_loss: 0.4905 - val_accuracy: 0.8409 - 35ms/epoch - 12ms/step
Epoch 36/50
3/3 - 0s - loss: 0.4543 - accuracy: 0.9101 - val_loss: 0.4786 - val_accuracy: 0.8636 - 33ms/epoch - 11ms/step
Epoch 37/50
3/3 - 0s - loss: 0.4290 - accuracy: 0.8989 - val_loss: 0.4673 - val_accuracy: 0.8636 - 33ms/epoch - 11ms/step
Epoch 38/50
3/3 - 0s - loss: 0.4131 - accuracy: 0.9101 - val_loss: 0.4563 - val_accuracy: 0.8636 - 35ms/epoch - 12ms/step
Epoch 39/50
3/3 - 0s - loss: 0.4263 - accuracy: 0.8989 - val_loss: 0.4464 - val_accuracy: 0.8636 - 56ms/epoch - 19ms/step
Epoch 40/50
3/3 - 0s - loss: 0.3975 - accuracy: 0.8876 - val_loss: 0.4370 - val_accuracy: 0.8636 - 63ms/epoch - 21ms/step
Epoch 41/50
3/3 - 0s - l

Epoch 39/50
3/3 - 0s - loss: 0.4950 - accuracy: 0.8409 - val_loss: 0.4990 - val_accuracy: 0.8889 - 32ms/epoch - 11ms/step
Epoch 40/50
3/3 - 0s - loss: 0.5210 - accuracy: 0.7727 - val_loss: 0.4841 - val_accuracy: 0.8889 - 33ms/epoch - 11ms/step
Epoch 41/50
3/3 - 0s - loss: 0.4814 - accuracy: 0.8636 - val_loss: 0.4709 - val_accuracy: 0.8889 - 32ms/epoch - 11ms/step
Epoch 42/50
3/3 - 0s - loss: 0.4930 - accuracy: 0.8523 - val_loss: 0.4568 - val_accuracy: 0.8889 - 33ms/epoch - 11ms/step
Epoch 43/50
3/3 - 0s - loss: 0.4800 - accuracy: 0.8295 - val_loss: 0.4438 - val_accuracy: 0.8889 - 32ms/epoch - 11ms/step
Epoch 44/50
3/3 - 0s - loss: 0.4545 - accuracy: 0.8864 - val_loss: 0.4317 - val_accuracy: 0.8889 - 33ms/epoch - 11ms/step
Epoch 45/50
3/3 - 0s - loss: 0.4492 - accuracy: 0.8977 - val_loss: 0.4208 - val_accuracy: 0.8889 - 32ms/epoch - 11ms/step
Epoch 46/50
3/3 - 0s - loss: 0.4246 - accuracy: 0.8864 - val_loss: 0.4115 - val_accuracy: 0.8889 - 33ms/epoch - 11ms/step
Epoch 47/50
3/3 - 0s - l

Epoch 7/50
3/3 - 0s - loss: 0.6930 - accuracy: 0.5281 - val_loss: 0.6675 - val_accuracy: 0.6364 - 35ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.7191 - accuracy: 0.5056 - val_loss: 0.6658 - val_accuracy: 0.6364 - 33ms/epoch - 11ms/step
Epoch 9/50
3/3 - 0s - loss: 0.6854 - accuracy: 0.5618 - val_loss: 0.6649 - val_accuracy: 0.6364 - 34ms/epoch - 11ms/step
Epoch 10/50
3/3 - 0s - loss: 0.6972 - accuracy: 0.5169 - val_loss: 0.6646 - val_accuracy: 0.6364 - 34ms/epoch - 11ms/step
Epoch 11/50
3/3 - 0s - loss: 0.6695 - accuracy: 0.5843 - val_loss: 0.6636 - val_accuracy: 0.6364 - 33ms/epoch - 11ms/step
Epoch 12/50
3/3 - 0s - loss: 0.7236 - accuracy: 0.4944 - val_loss: 0.6615 - val_accuracy: 0.6364 - 34ms/epoch - 11ms/step
Epoch 13/50
3/3 - 0s - loss: 0.7392 - accuracy: 0.4831 - val_loss: 0.6593 - val_accuracy: 0.6364 - 33ms/epoch - 11ms/step
Epoch 14/50
3/3 - 0s - loss: 0.6920 - accuracy: 0.5281 - val_loss: 0.6573 - val_accuracy: 0.6364 - 36ms/epoch - 12ms/step
Epoch 15/50
3/3 - 0s - loss

Epoch 24/50
3/3 - 0s - loss: 0.6872 - accuracy: 0.5568 - val_loss: 0.6903 - val_accuracy: 0.5111 - 34ms/epoch - 11ms/step
Epoch 25/50
3/3 - 0s - loss: 0.6618 - accuracy: 0.6250 - val_loss: 0.6867 - val_accuracy: 0.5111 - 36ms/epoch - 12ms/step
Epoch 26/50
3/3 - 0s - loss: 0.6946 - accuracy: 0.6136 - val_loss: 0.6830 - val_accuracy: 0.5111 - 34ms/epoch - 11ms/step
Epoch 27/50
3/3 - 0s - loss: 0.6986 - accuracy: 0.5795 - val_loss: 0.6800 - val_accuracy: 0.5111 - 34ms/epoch - 11ms/step
Epoch 28/50
3/3 - 0s - loss: 0.6356 - accuracy: 0.6477 - val_loss: 0.6769 - val_accuracy: 0.5111 - 35ms/epoch - 12ms/step
Epoch 29/50
3/3 - 0s - loss: 0.6312 - accuracy: 0.6705 - val_loss: 0.6734 - val_accuracy: 0.5111 - 32ms/epoch - 11ms/step
Epoch 30/50
3/3 - 0s - loss: 0.6586 - accuracy: 0.6364 - val_loss: 0.6698 - val_accuracy: 0.5111 - 34ms/epoch - 11ms/step
Epoch 31/50
3/3 - 0s - loss: 0.6682 - accuracy: 0.6364 - val_loss: 0.6655 - val_accuracy: 0.5111 - 34ms/epoch - 11ms/step
Epoch 32/50
3/3 - 0s - l

Epoch 42/50
3/3 - 0s - loss: 0.5080 - accuracy: 0.7079 - val_loss: 0.5192 - val_accuracy: 0.8636 - 34ms/epoch - 11ms/step
Epoch 43/50
3/3 - 0s - loss: 0.5566 - accuracy: 0.7640 - val_loss: 0.5095 - val_accuracy: 0.8409 - 32ms/epoch - 11ms/step
Epoch 44/50
3/3 - 0s - loss: 0.5559 - accuracy: 0.7079 - val_loss: 0.5002 - val_accuracy: 0.8409 - 33ms/epoch - 11ms/step
Epoch 45/50
3/3 - 0s - loss: 0.5112 - accuracy: 0.7865 - val_loss: 0.4913 - val_accuracy: 0.8409 - 33ms/epoch - 11ms/step
Epoch 46/50
3/3 - 0s - loss: 0.5016 - accuracy: 0.7865 - val_loss: 0.4828 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 47/50
3/3 - 0s - loss: 0.4574 - accuracy: 0.8315 - val_loss: 0.4742 - val_accuracy: 0.8636 - 33ms/epoch - 11ms/step
Epoch 48/50
3/3 - 0s - loss: 0.5469 - accuracy: 0.7865 - val_loss: 0.4656 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 49/50
3/3 - 0s - loss: 0.4577 - accuracy: 0.8315 - val_loss: 0.4571 - val_accuracy: 0.8636 - 32ms/epoch - 11ms/step
Epoch 50/50
3/3 - 0s - l

In [30]:
print(best_acc)
print(baseline_values)

0.9333333373069763
{'units': 32, 'activation': 'relu', 'kernel_size': 3, 'learning_rate': 1e-05, 'optimizer': 'RMSprop', 'dropout': 0.2}


In [31]:
#STOP

# 3 Prepare dataset

In [32]:
df = df_damage_sixteen_mean.drop(columns=columns)

X = df.drop(columns=['Damage'])
y = df['Damage']

# split the data into a holdout set and the rest for K-Fold cross-validation
X_train, X_holdout, y_train, y_holdout = train_test_split(X, y, train_size=training_percent, random_state=42)

In [33]:
# Initialize StandardScaler
scaler = StandardScaler()

# Fit scaler on training data
scaler.fit(X_train)

# Transform both training and test data
X_train_scaled = scaler.transform(X_train)
X_holdout_scaled = scaler.transform(X_holdout)

In [34]:
best_acc = 0.0
baseline_values = { 'units': 0, 'activation': '', 'kernel_size': 0, 'learning_rate' : 0.0, 'optimizer': '', 'dropout': 0.0 }

In [35]:
input_dim = X_train.shape[1]

In [36]:
for u in units:
    for a in activations:
        for k in kernel_size:
            for l in learning_rate:
                for o in optimizer:
                    for d in dropout:
                        print('\nUnits:', u, 'Activation:', a, 'Kernel size:', k, 'Learning rate:', l, 'Optimizer:', o, 'Dropout:', d)
                        for train_index, val_index in kf.split(X_train_scaled):
                            # split the dataset into training and validation sets for this fold
                            X_train_kf, X_val_kf = X_train_scaled[train_index], X_train_scaled[val_index]
                            y_train_kf, y_val_kf = y_train.iloc[train_index], y_train.iloc[val_index]

                            model = Baseline(input_dim, u, a, k, l, o, d)

                            history = model.train(X_train_kf, y_train_kf, X_val_kf, y_val_kf, epochs, batch_size)
                            if (history.history['val_accuracy'][-1] > best_acc):
                                best_acc = history.history['val_accuracy'][-1]
                                baseline_values = { 'units': u, 'activation': a, 'kernel_size': k, 'learning_rate' : l, 'optimizer': o, 'dropout': d }


Units: 32 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: Adam Dropout: 0.1
Epoch 1/50
3/3 - 1s - loss: 0.6861 - accuracy: 0.5455 - val_loss: 0.6759 - val_accuracy: 0.6000 - 1s/epoch - 349ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6740 - accuracy: 0.5227 - val_loss: 0.6635 - val_accuracy: 0.5778 - 33ms/epoch - 11ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6526 - accuracy: 0.6136 - val_loss: 0.6562 - val_accuracy: 0.5778 - 32ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6604 - accuracy: 0.6136 - val_loss: 0.6502 - val_accuracy: 0.5556 - 33ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6526 - accuracy: 0.6136 - val_loss: 0.6461 - val_accuracy: 0.5333 - 33ms/epoch - 11ms/step
Epoch 6/50
3/3 - 0s - loss: 0.6269 - accuracy: 0.6250 - val_loss: 0.6436 - val_accuracy: 0.5333 - 32ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6288 - accuracy: 0.5795 - val_loss: 0.6427 - val_accuracy: 0.5333 - 32ms/epoch - 11ms/step
Epoch 8/50
3/3 - 0s - loss: 0.6243 - accuracy: 0.6705 - val_l

Epoch 39/50
3/3 - 0s - loss: 0.4852 - accuracy: 0.8090 - val_loss: 0.5454 - val_accuracy: 0.7500 - 31ms/epoch - 10ms/step
Epoch 40/50
3/3 - 0s - loss: 0.4541 - accuracy: 0.7753 - val_loss: 0.5414 - val_accuracy: 0.7500 - 31ms/epoch - 10ms/step
Epoch 41/50
3/3 - 0s - loss: 0.4483 - accuracy: 0.8202 - val_loss: 0.5416 - val_accuracy: 0.7500 - 30ms/epoch - 10ms/step
Epoch 42/50
3/3 - 0s - loss: 0.4730 - accuracy: 0.7640 - val_loss: 0.5378 - val_accuracy: 0.7500 - 31ms/epoch - 10ms/step
Epoch 43/50
3/3 - 0s - loss: 0.4809 - accuracy: 0.8202 - val_loss: 0.5322 - val_accuracy: 0.7500 - 31ms/epoch - 10ms/step
Epoch 44/50
3/3 - 0s - loss: 0.4845 - accuracy: 0.7753 - val_loss: 0.5278 - val_accuracy: 0.7727 - 32ms/epoch - 11ms/step
Epoch 45/50
3/3 - 0s - loss: 0.4491 - accuracy: 0.8202 - val_loss: 0.5226 - val_accuracy: 0.7955 - 34ms/epoch - 11ms/step
Epoch 46/50
3/3 - 0s - loss: 0.4167 - accuracy: 0.8202 - val_loss: 0.5260 - val_accuracy: 0.7727 - 31ms/epoch - 10ms/step
Epoch 47/50
3/3 - 0s - l

Epoch 34/50
3/3 - 0s - loss: 0.6120 - accuracy: 0.6364 - val_loss: 0.6168 - val_accuracy: 0.6000 - 32ms/epoch - 11ms/step
Epoch 35/50
3/3 - 0s - loss: 0.5939 - accuracy: 0.6932 - val_loss: 0.6161 - val_accuracy: 0.6000 - 31ms/epoch - 10ms/step
Epoch 36/50
3/3 - 0s - loss: 0.6258 - accuracy: 0.6705 - val_loss: 0.6154 - val_accuracy: 0.6000 - 31ms/epoch - 10ms/step
Epoch 37/50
3/3 - 0s - loss: 0.5963 - accuracy: 0.6705 - val_loss: 0.6146 - val_accuracy: 0.6222 - 32ms/epoch - 11ms/step
Epoch 38/50
3/3 - 0s - loss: 0.5776 - accuracy: 0.6705 - val_loss: 0.6131 - val_accuracy: 0.6222 - 32ms/epoch - 11ms/step
Epoch 39/50
3/3 - 0s - loss: 0.5878 - accuracy: 0.6818 - val_loss: 0.6112 - val_accuracy: 0.6667 - 30ms/epoch - 10ms/step
Epoch 40/50
3/3 - 0s - loss: 0.6034 - accuracy: 0.6932 - val_loss: 0.6086 - val_accuracy: 0.6667 - 31ms/epoch - 10ms/step
Epoch 41/50
3/3 - 0s - loss: 0.6108 - accuracy: 0.7159 - val_loss: 0.6065 - val_accuracy: 0.6889 - 32ms/epoch - 11ms/step
Epoch 42/50
3/3 - 0s - l

Epoch 25/50
3/3 - 0s - loss: 0.5716 - accuracy: 0.7303 - val_loss: 0.6081 - val_accuracy: 0.6818 - 36ms/epoch - 12ms/step
Epoch 26/50
3/3 - 0s - loss: 0.6036 - accuracy: 0.6966 - val_loss: 0.6057 - val_accuracy: 0.6818 - 33ms/epoch - 11ms/step
Epoch 27/50
3/3 - 0s - loss: 0.6462 - accuracy: 0.6292 - val_loss: 0.6037 - val_accuracy: 0.6818 - 34ms/epoch - 11ms/step
Epoch 28/50
3/3 - 0s - loss: 0.6113 - accuracy: 0.6404 - val_loss: 0.6016 - val_accuracy: 0.6818 - 35ms/epoch - 12ms/step
Epoch 29/50
3/3 - 0s - loss: 0.6014 - accuracy: 0.6629 - val_loss: 0.5992 - val_accuracy: 0.6818 - 34ms/epoch - 11ms/step
Epoch 30/50
3/3 - 0s - loss: 0.6070 - accuracy: 0.6966 - val_loss: 0.5989 - val_accuracy: 0.6818 - 33ms/epoch - 11ms/step
Epoch 31/50
3/3 - 0s - loss: 0.6166 - accuracy: 0.6180 - val_loss: 0.5983 - val_accuracy: 0.6591 - 34ms/epoch - 11ms/step
Epoch 32/50
3/3 - 0s - loss: 0.5901 - accuracy: 0.6742 - val_loss: 0.5972 - val_accuracy: 0.6591 - 35ms/epoch - 12ms/step
Epoch 33/50
3/3 - 0s - l

Epoch 18/50
3/3 - 0s - loss: 0.6414 - accuracy: 0.6966 - val_loss: 0.6511 - val_accuracy: 0.5909 - 33ms/epoch - 11ms/step
Epoch 19/50
3/3 - 0s - loss: 0.6383 - accuracy: 0.6180 - val_loss: 0.6504 - val_accuracy: 0.5909 - 33ms/epoch - 11ms/step
Epoch 20/50
3/3 - 0s - loss: 0.7016 - accuracy: 0.5730 - val_loss: 0.6498 - val_accuracy: 0.5909 - 33ms/epoch - 11ms/step
Epoch 21/50
3/3 - 0s - loss: 0.6618 - accuracy: 0.6180 - val_loss: 0.6489 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 22/50
3/3 - 0s - loss: 0.6512 - accuracy: 0.6404 - val_loss: 0.6478 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 23/50
3/3 - 0s - loss: 0.6506 - accuracy: 0.6404 - val_loss: 0.6468 - val_accuracy: 0.6136 - 32ms/epoch - 11ms/step
Epoch 24/50
3/3 - 0s - loss: 0.6604 - accuracy: 0.6067 - val_loss: 0.6459 - val_accuracy: 0.6136 - 32ms/epoch - 11ms/step
Epoch 25/50
3/3 - 0s - loss: 0.6131 - accuracy: 0.6517 - val_loss: 0.6454 - val_accuracy: 0.6136 - 34ms/epoch - 11ms/step
Epoch 26/50
3/3 - 0s - l

...

Epoch 8/50
3/3 - 0s - loss: 0.7425 - accuracy: 0.5618 - val_loss: 0.7169 - val_accuracy: 0.5227 - 36ms/epoch - 12ms/step
Epoch 9/50
3/3 - 0s - loss: 0.6983 - accuracy: 0.5618 - val_loss: 0.7140 - val_accuracy: 0.5227 - 34ms/epoch - 11ms/step
Epoch 10/50
3/3 - 0s - loss: 0.7387 - accuracy: 0.5618 - val_loss: 0.7116 - val_accuracy: 0.5227 - 34ms/epoch - 11ms/step
Epoch 11/50
3/3 - 0s - loss: 0.7183 - accuracy: 0.5056 - val_loss: 0.7086 - val_accuracy: 0.5227 - 38ms/epoch - 13ms/step
Epoch 12/50
3/3 - 0s - loss: 0.7109 - accuracy: 0.6067 - val_loss: 0.7062 - val_accuracy: 0.5227 - 37ms/epoch - 12ms/step
Epoch 13/50
3/3 - 0s - loss: 0.7019 - accuracy: 0.5618 - val_loss: 0.7047 - val_accuracy: 0.5227 - 61ms/epoch - 20ms/step
Epoch 14/50
3/3 - 0s - loss: 0.6557 - accuracy: 0.5955 - val_loss: 0.7040 - val_accuracy: 0.5227 - 36ms/epoch - 12ms/step
Epoch 15/50
3/3 - 0s - loss: 0.6864 - accuracy: 0.5955 - val_loss: 0.7045 - val_accuracy: 0.5227 - 35ms/epoch - 12ms/step
Epoch 16/50
3/3 - 0s - los

Epoch 14/50
3/3 - 0s - loss: 0.7022 - accuracy: 0.5114 - val_loss: 0.6897 - val_accuracy: 0.5778 - 43ms/epoch - 14ms/step
Epoch 15/50
3/3 - 0s - loss: 0.6937 - accuracy: 0.5227 - val_loss: 0.6858 - val_accuracy: 0.5778 - 43ms/epoch - 14ms/step
Epoch 16/50
3/3 - 0s - loss: 0.6931 - accuracy: 0.4886 - val_loss: 0.6830 - val_accuracy: 0.5778 - 53ms/epoch - 18ms/step
Epoch 17/50
3/3 - 0s - loss: 0.7008 - accuracy: 0.5341 - val_loss: 0.6813 - val_accuracy: 0.5778 - 46ms/epoch - 15ms/step
Epoch 18/50
3/3 - 0s - loss: 0.6845 - accuracy: 0.6136 - val_loss: 0.6803 - val_accuracy: 0.5778 - 43ms/epoch - 14ms/step
Epoch 19/50
3/3 - 0s - loss: 0.7006 - accuracy: 0.5455 - val_loss: 0.6797 - val_accuracy: 0.5778 - 39ms/epoch - 13ms/step
Epoch 20/50
3/3 - 0s - loss: 0.6969 - accuracy: 0.5455 - val_loss: 0.6793 - val_accuracy: 0.5778 - 41ms/epoch - 14ms/step
Epoch 21/50
3/3 - 0s - loss: 0.7094 - accuracy: 0.5227 - val_loss: 0.6791 - val_accuracy: 0.5778 - 39ms/epoch - 13ms/step
Epoch 22/50
3/3 - 0s - l

Epoch 5/50
3/3 - 0s - loss: 0.7180 - accuracy: 0.5506 - val_loss: 0.6732 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 6/50
3/3 - 0s - loss: 0.7177 - accuracy: 0.5506 - val_loss: 0.6692 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6975 - accuracy: 0.5506 - val_loss: 0.6671 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.7115 - accuracy: 0.5506 - val_loss: 0.6670 - val_accuracy: 0.6136 - 35ms/epoch - 12ms/step
Epoch 9/50
3/3 - 0s - loss: 0.7106 - accuracy: 0.5056 - val_loss: 0.6681 - val_accuracy: 0.6136 - 37ms/epoch - 12ms/step
Epoch 10/50
3/3 - 0s - loss: 0.7080 - accuracy: 0.5393 - val_loss: 0.6700 - val_accuracy: 0.6136 - 36ms/epoch - 12ms/step
Epoch 11/50
3/3 - 0s - loss: 0.7179 - accuracy: 0.4607 - val_loss: 0.6723 - val_accuracy: 0.6136 - 38ms/epoch - 13ms/step
Epoch 12/50
3/3 - 0s - loss: 0.7178 - accuracy: 0.5056 - val_loss: 0.6745 - val_accuracy: 0.6136 - 36ms/epoch - 12ms/step
Epoch 13/50
3/3 - 0s - loss: 

Epoch 4/50
3/3 - 0s - loss: 0.6972 - accuracy: 0.5281 - val_loss: 0.6957 - val_accuracy: 0.4773 - 33ms/epoch - 11ms/step
Epoch 5/50
3/3 - 0s - loss: 0.7311 - accuracy: 0.4494 - val_loss: 0.6924 - val_accuracy: 0.5682 - 36ms/epoch - 12ms/step
Epoch 6/50
3/3 - 0s - loss: 0.7176 - accuracy: 0.4719 - val_loss: 0.6912 - val_accuracy: 0.5227 - 34ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6992 - accuracy: 0.4831 - val_loss: 0.6922 - val_accuracy: 0.5227 - 33ms/epoch - 11ms/step
Epoch 8/50
3/3 - 0s - loss: 0.7377 - accuracy: 0.4719 - val_loss: 0.6945 - val_accuracy: 0.5227 - 38ms/epoch - 13ms/step
Epoch 9/50
3/3 - 0s - loss: 0.6988 - accuracy: 0.5393 - val_loss: 0.6975 - val_accuracy: 0.5227 - 35ms/epoch - 12ms/step
Epoch 10/50
3/3 - 0s - loss: 0.6866 - accuracy: 0.5506 - val_loss: 0.7005 - val_accuracy: 0.5227 - 132ms/epoch - 44ms/step
Epoch 11/50
3/3 - 0s - loss: 0.6670 - accuracy: 0.5506 - val_loss: 0.7043 - val_accuracy: 0.5227 - 36ms/epoch - 12ms/step
Epoch 12/50
3/3 - 0s - loss: 

Epoch 35/50
3/3 - 0s - loss: 0.6909 - accuracy: 0.5114 - val_loss: 0.6777 - val_accuracy: 0.5778 - 34ms/epoch - 11ms/step
Epoch 36/50
3/3 - 0s - loss: 0.6621 - accuracy: 0.6136 - val_loss: 0.6776 - val_accuracy: 0.5778 - 32ms/epoch - 11ms/step
Epoch 37/50
3/3 - 0s - loss: 0.6868 - accuracy: 0.5568 - val_loss: 0.6775 - val_accuracy: 0.5778 - 35ms/epoch - 12ms/step
Epoch 38/50
3/3 - 0s - loss: 0.7315 - accuracy: 0.4545 - val_loss: 0.6774 - val_accuracy: 0.5778 - 34ms/epoch - 11ms/step
Epoch 39/50
3/3 - 0s - loss: 0.6653 - accuracy: 0.5909 - val_loss: 0.6774 - val_accuracy: 0.5778 - 36ms/epoch - 12ms/step
Epoch 40/50
3/3 - 0s - loss: 0.7379 - accuracy: 0.5341 - val_loss: 0.6774 - val_accuracy: 0.5778 - 33ms/epoch - 11ms/step
Epoch 41/50
3/3 - 0s - loss: 0.6916 - accuracy: 0.5568 - val_loss: 0.6775 - val_accuracy: 0.5778 - 34ms/epoch - 11ms/step
Epoch 42/50
3/3 - 0s - loss: 0.7173 - accuracy: 0.4545 - val_loss: 0.6774 - val_accuracy: 0.5778 - 33ms/epoch - 11ms/step
Epoch 43/50
3/3 - 0s - l

In [37]:
print(best_acc)
print(baseline_values)

0.7954545617103577
{'units': 32, 'activation': 'tanh', 'kernel_size': 3, 'learning_rate': 0.001, 'optimizer': 'RMSprop', 'dropout': 0.2}


In [38]:
#STOP

# 4 Prepare dataset

In [39]:
df = df_damage_thirtytwo_mean.drop(columns=columns)

X = df.drop(columns=['Damage'])
y = df['Damage']

# split the data into a holdout set and the rest for K-Fold cross-validation
X_train, X_holdout, y_train, y_holdout = train_test_split(X, y, train_size=training_percent, random_state=42)

In [40]:
# Initialize StandardScaler
scaler = StandardScaler()

# Fit scaler on training data
scaler.fit(X_train)

# Transform both training and test data
X_train_scaled = scaler.transform(X_train)
X_holdout_scaled = scaler.transform(X_holdout)

In [41]:
best_acc = 0.0
baseline_values = { 'units': 0, 'activation': '', 'kernel_size': 0, 'learning_rate' : 0.0, 'optimizer': '', 'dropout': 0.0 }

In [42]:
input_dim = X_train.shape[1]

In [43]:
for u in units:
    for a in activations:
        for k in kernel_size:
            for l in learning_rate:
                for o in optimizer:
                    for d in dropout:
                        print('\nUnits:', u, 'Activation:', a, 'Kernel size:', k, 'Learning rate:', l, 'Optimizer:', o, 'Dropout:', d)
                        for train_index, val_index in kf.split(X_train_scaled):
                            # split the dataset into training and validation sets for this fold
                            X_train_kf, X_val_kf = X_train_scaled[train_index], X_train_scaled[val_index]
                            y_train_kf, y_val_kf = y_train.iloc[train_index], y_train.iloc[val_index]

                            model = Baseline(input_dim, u, a, k, l, o, d)

                            history = model.train(X_train_kf, y_train_kf, X_val_kf, y_val_kf, epochs, batch_size)
                            if (history.history['val_accuracy'][-1] > best_acc):
                                best_acc = history.history['val_accuracy'][-1]
                                baseline_values = { 'units': u, 'activation': a, 'kernel_size': k, 'learning_rate' : l, 'optimizer': o, 'dropout': d }


Units: 32 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: Adam Dropout: 0.1
Epoch 1/50
3/3 - 1s - loss: 0.7385 - accuracy: 0.4773 - val_loss: 0.7176 - val_accuracy: 0.4222 - 1s/epoch - 410ms/step
Epoch 2/50
3/3 - 0s - loss: 0.7143 - accuracy: 0.4432 - val_loss: 0.7028 - val_accuracy: 0.5778 - 33ms/epoch - 11ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6916 - accuracy: 0.5455 - val_loss: 0.6944 - val_accuracy: 0.6000 - 34ms/epoch - 11ms/step
Epoch 4/50
3/3 - 0s - loss: 0.6829 - accuracy: 0.4659 - val_loss: 0.6914 - val_accuracy: 0.5556 - 37ms/epoch - 12ms/step
Epoch 5/50
3/3 - 0s - loss: 0.6673 - accuracy: 0.5568 - val_loss: 0.6881 - val_accuracy: 0.5111 - 35ms/epoch - 12ms/step
Epoch 6/50
3/3 - 0s - loss: 0.6650 - accuracy: 0.5341 - val_loss: 0.6864 - val_accuracy: 0.5556 - 34ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6750 - accuracy: 0.5909 - val_loss: 0.6851 - val_accuracy: 0.5778 - 38ms/epoch - 13ms/step
Epoch 8/50
3/3 - 0s - loss: 0.6740 - accuracy: 0.5568 - val_l

Epoch 7/50
3/3 - 0s - loss: 0.6643 - accuracy: 0.6067 - val_loss: 0.6383 - val_accuracy: 0.6364 - 35ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.6814 - accuracy: 0.6292 - val_loss: 0.6370 - val_accuracy: 0.6364 - 33ms/epoch - 11ms/step
Epoch 9/50
3/3 - 0s - loss: 0.6766 - accuracy: 0.5843 - val_loss: 0.6321 - val_accuracy: 0.6364 - 34ms/epoch - 11ms/step
Epoch 10/50
3/3 - 0s - loss: 0.6690 - accuracy: 0.6067 - val_loss: 0.6290 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 11/50
3/3 - 0s - loss: 0.6547 - accuracy: 0.6404 - val_loss: 0.6272 - val_accuracy: 0.6136 - 33ms/epoch - 11ms/step
Epoch 12/50
3/3 - 0s - loss: 0.6711 - accuracy: 0.5730 - val_loss: 0.6264 - val_accuracy: 0.5909 - 33ms/epoch - 11ms/step
Epoch 13/50
3/3 - 0s - loss: 0.6523 - accuracy: 0.6180 - val_loss: 0.6271 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 14/50
3/3 - 0s - loss: 0.6519 - accuracy: 0.5730 - val_loss: 0.6275 - val_accuracy: 0.6591 - 35ms/epoch - 12ms/step
Epoch 15/50
3/3 - 0s - loss

Epoch 24/50
3/3 - 0s - loss: 0.6394 - accuracy: 0.6591 - val_loss: 0.6543 - val_accuracy: 0.6000 - 32ms/epoch - 11ms/step
Epoch 25/50
3/3 - 0s - loss: 0.6226 - accuracy: 0.6364 - val_loss: 0.6524 - val_accuracy: 0.6000 - 34ms/epoch - 11ms/step
Epoch 26/50
3/3 - 0s - loss: 0.5929 - accuracy: 0.7273 - val_loss: 0.6507 - val_accuracy: 0.6222 - 33ms/epoch - 11ms/step
Epoch 27/50
3/3 - 0s - loss: 0.6122 - accuracy: 0.6705 - val_loss: 0.6503 - val_accuracy: 0.6222 - 35ms/epoch - 12ms/step
Epoch 28/50
3/3 - 0s - loss: 0.6190 - accuracy: 0.7045 - val_loss: 0.6512 - val_accuracy: 0.6000 - 33ms/epoch - 11ms/step
Epoch 29/50
3/3 - 0s - loss: 0.6309 - accuracy: 0.6477 - val_loss: 0.6504 - val_accuracy: 0.6222 - 34ms/epoch - 11ms/step
Epoch 30/50
3/3 - 0s - loss: 0.5897 - accuracy: 0.6932 - val_loss: 0.6502 - val_accuracy: 0.6000 - 39ms/epoch - 13ms/step
Epoch 31/50
3/3 - 0s - loss: 0.5991 - accuracy: 0.7159 - val_loss: 0.6494 - val_accuracy: 0.6444 - 34ms/epoch - 11ms/step
Epoch 32/50
3/3 - 0s - l

Epoch 20/50
3/3 - 0s - loss: 0.6526 - accuracy: 0.5506 - val_loss: 0.6387 - val_accuracy: 0.5909 - 33ms/epoch - 11ms/step
Epoch 21/50
3/3 - 0s - loss: 0.6338 - accuracy: 0.5955 - val_loss: 0.6380 - val_accuracy: 0.5909 - 35ms/epoch - 12ms/step
Epoch 22/50
3/3 - 0s - loss: 0.6304 - accuracy: 0.6067 - val_loss: 0.6373 - val_accuracy: 0.5909 - 39ms/epoch - 13ms/step
Epoch 23/50
3/3 - 0s - loss: 0.6227 - accuracy: 0.5730 - val_loss: 0.6374 - val_accuracy: 0.5909 - 40ms/epoch - 13ms/step

Units: 32 Activation: relu Kernel size: 3 Learning rate: 0.001 Optimizer: Adam Dropout: 0.3
Epoch 1/50
3/3 - 1s - loss: 0.7008 - accuracy: 0.5455 - val_loss: 0.6757 - val_accuracy: 0.7111 - 1s/epoch - 387ms/step
Epoch 2/50
3/3 - 0s - loss: 0.6939 - accuracy: 0.5114 - val_loss: 0.6721 - val_accuracy: 0.6444 - 37ms/epoch - 12ms/step
Epoch 3/50
3/3 - 0s - loss: 0.6860 - accuracy: 0.5682 - val_loss: 0.6695 - val_accuracy: 0.6222 - 35ms/epoch - 12ms/step
Epoch 4/50
3/3 - 0s - loss: 0.7053 - accuracy: 0.5341 - v

Epoch 15/50
3/3 - 0s - loss: 0.6343 - accuracy: 0.6292 - val_loss: 0.6953 - val_accuracy: 0.5227 - 32ms/epoch - 11ms/step
Epoch 16/50
3/3 - 0s - loss: 0.6353 - accuracy: 0.6404 - val_loss: 0.6953 - val_accuracy: 0.5455 - 32ms/epoch - 11ms/step
Epoch 17/50
3/3 - 0s - loss: 0.6735 - accuracy: 0.5393 - val_loss: 0.6956 - val_accuracy: 0.5455 - 31ms/epoch - 10ms/step
Epoch 18/50
3/3 - 0s - loss: 0.6605 - accuracy: 0.5843 - val_loss: 0.6960 - val_accuracy: 0.5455 - 33ms/epoch - 11ms/step
Epoch 19/50
3/3 - 0s - loss: 0.6716 - accuracy: 0.6180 - val_loss: 0.6949 - val_accuracy: 0.5227 - 32ms/epoch - 11ms/step
Epoch 20/50
3/3 - 0s - loss: 0.6522 - accuracy: 0.5730 - val_loss: 0.6944 - val_accuracy: 0.5227 - 35ms/epoch - 12ms/step
Epoch 21/50
3/3 - 0s - loss: 0.6756 - accuracy: 0.5506 - val_loss: 0.6943 - val_accuracy: 0.5227 - 34ms/epoch - 11ms/step
Epoch 22/50
3/3 - 0s - loss: 0.6765 - accuracy: 0.6067 - val_loss: 0.6941 - val_accuracy: 0.5227 - 35ms/epoch - 12ms/step
Epoch 23/50
3/3 - 0s - l

...

Epoch 6/50
3/3 - 0s - loss: 0.7021 - accuracy: 0.5056 - val_loss: 0.6941 - val_accuracy: 0.4091 - 34ms/epoch - 11ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6981 - accuracy: 0.4944 - val_loss: 0.6903 - val_accuracy: 0.5909 - 33ms/epoch - 11ms/step
Epoch 8/50
3/3 - 0s - loss: 0.7083 - accuracy: 0.4831 - val_loss: 0.6880 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 9/50
3/3 - 0s - loss: 0.7024 - accuracy: 0.5730 - val_loss: 0.6854 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 10/50
3/3 - 0s - loss: 0.6973 - accuracy: 0.5281 - val_loss: 0.6841 - val_accuracy: 0.5909 - 33ms/epoch - 11ms/step
Epoch 11/50
3/3 - 0s - loss: 0.7094 - accuracy: 0.4944 - val_loss: 0.6832 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 12/50
3/3 - 0s - loss: 0.6974 - accuracy: 0.5393 - val_loss: 0.6813 - val_accuracy: 0.5909 - 35ms/epoch - 12ms/step
Epoch 13/50
3/3 - 0s - loss: 0.7065 - accuracy: 0.5618 - val_loss: 0.6794 - val_accuracy: 0.5909 - 34ms/epoch - 11ms/step
Epoch 14/50
3/3 - 0s - loss:

Epoch 5/50
3/3 - 0s - loss: 0.6775 - accuracy: 0.5843 - val_loss: 0.6921 - val_accuracy: 0.5227 - 37ms/epoch - 12ms/step
Epoch 6/50
3/3 - 0s - loss: 0.7432 - accuracy: 0.5169 - val_loss: 0.6924 - val_accuracy: 0.5227 - 37ms/epoch - 12ms/step
Epoch 7/50
3/3 - 0s - loss: 0.7317 - accuracy: 0.4719 - val_loss: 0.6935 - val_accuracy: 0.5227 - 35ms/epoch - 12ms/step
Epoch 8/50
3/3 - 0s - loss: 0.7023 - accuracy: 0.5843 - val_loss: 0.6946 - val_accuracy: 0.5227 - 38ms/epoch - 13ms/step
Epoch 9/50
3/3 - 0s - loss: 0.6913 - accuracy: 0.4944 - val_loss: 0.6951 - val_accuracy: 0.5227 - 36ms/epoch - 12ms/step
Epoch 10/50
3/3 - 0s - loss: 0.7347 - accuracy: 0.4494 - val_loss: 0.6973 - val_accuracy: 0.5227 - 36ms/epoch - 12ms/step
Epoch 11/50
3/3 - 0s - loss: 0.6957 - accuracy: 0.4944 - val_loss: 0.6973 - val_accuracy: 0.5227 - 36ms/epoch - 12ms/step
Epoch 12/50
3/3 - 0s - loss: 0.7183 - accuracy: 0.4944 - val_loss: 0.6971 - val_accuracy: 0.5227 - 38ms/epoch - 13ms/step
Epoch 13/50
3/3 - 0s - loss: 

Epoch 1/50
3/3 - 3s - loss: 0.7854 - accuracy: 0.5506 - val_loss: 0.7096 - val_accuracy: 0.5909 - 3s/epoch - 1s/step
Epoch 2/50
3/3 - 0s - loss: 0.7481 - accuracy: 0.5506 - val_loss: 0.7002 - val_accuracy: 0.5909 - 40ms/epoch - 13ms/step
Epoch 3/50
3/3 - 0s - loss: 0.7436 - accuracy: 0.5506 - val_loss: 0.6918 - val_accuracy: 0.5909 - 48ms/epoch - 16ms/step
Epoch 4/50
3/3 - 0s - loss: 0.7118 - accuracy: 0.5618 - val_loss: 0.6853 - val_accuracy: 0.5909 - 44ms/epoch - 15ms/step
Epoch 5/50
3/3 - 0s - loss: 0.7034 - accuracy: 0.5506 - val_loss: 0.6804 - val_accuracy: 0.5909 - 45ms/epoch - 15ms/step
Epoch 6/50
3/3 - 0s - loss: 0.7126 - accuracy: 0.5618 - val_loss: 0.6773 - val_accuracy: 0.5909 - 40ms/epoch - 13ms/step
Epoch 7/50
3/3 - 0s - loss: 0.6927 - accuracy: 0.5618 - val_loss: 0.6759 - val_accuracy: 0.5909 - 40ms/epoch - 13ms/step
Epoch 8/50
3/3 - 0s - loss: 0.6893 - accuracy: 0.5730 - val_loss: 0.6756 - val_accuracy: 0.5909 - 39ms/epoch - 13ms/step
Epoch 9/50
3/3 - 0s - loss: 0.7078 -

Epoch 11/50
3/3 - 0s - loss: 0.6971 - accuracy: 0.5506 - val_loss: 0.6972 - val_accuracy: 0.5227 - 42ms/epoch - 14ms/step
Epoch 12/50
3/3 - 0s - loss: 0.6704 - accuracy: 0.5730 - val_loss: 0.6972 - val_accuracy: 0.5227 - 40ms/epoch - 13ms/step
Epoch 13/50
3/3 - 0s - loss: 0.6954 - accuracy: 0.5843 - val_loss: 0.6978 - val_accuracy: 0.5227 - 40ms/epoch - 13ms/step
Epoch 14/50
3/3 - 0s - loss: 0.6536 - accuracy: 0.6404 - val_loss: 0.6987 - val_accuracy: 0.5227 - 39ms/epoch - 13ms/step
Epoch 15/50
3/3 - 0s - loss: 0.6982 - accuracy: 0.5730 - val_loss: 0.6993 - val_accuracy: 0.5227 - 41ms/epoch - 14ms/step
Epoch 16/50
3/3 - 0s - loss: 0.7074 - accuracy: 0.5618 - val_loss: 0.6993 - val_accuracy: 0.5227 - 37ms/epoch - 12ms/step
Epoch 17/50
3/3 - 0s - loss: 0.7027 - accuracy: 0.5393 - val_loss: 0.6989 - val_accuracy: 0.5227 - 35ms/epoch - 12ms/step
Epoch 18/50
3/3 - 0s - loss: 0.7005 - accuracy: 0.5843 - val_loss: 0.6995 - val_accuracy: 0.5227 - 36ms/epoch - 12ms/step
Epoch 19/50
3/3 - 0s - l

Epoch 13/50
3/3 - 0s - loss: 0.7123 - accuracy: 0.4659 - val_loss: 0.6805 - val_accuracy: 0.5778 - 42ms/epoch - 14ms/step
Epoch 14/50
3/3 - 0s - loss: 0.6507 - accuracy: 0.5795 - val_loss: 0.6807 - val_accuracy: 0.5778 - 37ms/epoch - 12ms/step
Epoch 15/50
3/3 - 0s - loss: 0.7621 - accuracy: 0.4886 - val_loss: 0.6812 - val_accuracy: 0.5778 - 35ms/epoch - 12ms/step
Epoch 16/50
3/3 - 0s - loss: 0.7319 - accuracy: 0.5000 - val_loss: 0.6819 - val_accuracy: 0.5778 - 38ms/epoch - 13ms/step
Epoch 17/50
3/3 - 0s - loss: 0.6917 - accuracy: 0.5568 - val_loss: 0.6824 - val_accuracy: 0.5778 - 43ms/epoch - 14ms/step
Epoch 18/50
3/3 - 0s - loss: 0.6909 - accuracy: 0.5114 - val_loss: 0.6829 - val_accuracy: 0.5778 - 46ms/epoch - 15ms/step
Epoch 19/50
3/3 - 0s - loss: 0.7234 - accuracy: 0.4545 - val_loss: 0.6829 - val_accuracy: 0.5778 - 42ms/epoch - 14ms/step
Epoch 20/50
3/3 - 0s - loss: 0.6929 - accuracy: 0.5568 - val_loss: 0.6826 - val_accuracy: 0.5778 - 43ms/epoch - 14ms/step
Epoch 21/50
3/3 - 0s - l

In [44]:
print(best_acc)
print(baseline_values)

0.7555555701255798
{'units': 32, 'activation': 'relu', 'kernel_size': 3, 'learning_rate': 0.001, 'optimizer': 'Adam', 'dropout': 0.1}


In [45]:
#STOP